# [Coin Partitions](https://projecteuler.net/problem=78)

SageMath once again makes this pretty trivial.

In [1]:
from itertools import count

for n in count(1):
    if number_of_partitions(n) % 1000000 == 0:
        break

n

55374

Theoretically, we could create a generating function like we did in [problem 31](https://projecteuler.net/problem=76) or [problem 76](https://projecteuler.net/problem=76) to solve this, and could even use $\mathbb{Z}_{1000000}$ as our base ring to handle the modulus automagically, but since the answer is pretty large, it would be impractical to construct the function with the required precision.

Instead, if you'd like to implement the [partition function](https://en.wikipedia.org/wiki/Partition_function_(number_theory)) yourself, Euler's [pentagonal number theorem](https://en.wikipedia.org/wiki/Pentagonal_number_theorem) leads to a useful recurrence equation:
$$p(n) = p(n - 1) + p(n - 2) - p(n - 5) - p(n - 7) + p(n - 12) + p(n - 15) - p(n - 22) - p(n - 26) + \cdots$$
Here, the numbers are the [generalized pentagonal numbers](https://en.wikipedia.org/wiki/Pentagonal_number). As base cases, $p(0) = 1$ and $p(n) = 0$ for negative $n$, so the infinite series eventually converges.

We can directly translate this equation into an implementation.

In [2]:
from functools import cache

@cache
def p(n, modulus):
    if n < 0:
        return 0
    
    if n == 0:
        return 1
    
    total = 0
    limit = floor((1 + sqrt(1+24*n)) / 6)
    
    # we reverse the range so smaller p(n) values are calculated first and cached
    # this helps avoid hitting Python's maximum recursion depth
    for k in reversed(range(1, limit + 1)):
        total += (-1)^(k+1) * (p(n - polygonal_number(5, k), modulus) + p(n - polygonal_number(5, -k), modulus))
        total %= modulus
    
    return total

Note that SageMath uses libraries like [FLINT](https://flintlib.org/doc/partitions.html) with faster - but much more technical - methods, like the Hardy-Ramanujan-Rademacher formula. This implementation is much easier to both understand and write, but is less performant.

## Relevant sequences
* Partition numbers: [A000041](https://oeis.org/A000041)
* Generalized pentagonal numbers: [A001318](https://oeis.org/A001318)